In [8]:
import orjson
import ijson

from tqdm import tqdm

In [3]:
data_path = "output/Qwen3-Coder-30B-A3B/Scenario.codegeneration_10_0.2_eval_all.json"
out_path = "output/Qwen3-Coder-30B-A3B/Scenario.codegeneration_10_0.2_eval_all.jsonl"
jsonlines = "output/Qwen3-Coder-30B-A3B/codegeneration_10_0.2_eval_all.jsonl"

In [4]:


# convert to jsonl
def clean_logprobs(logprobs_list):
    for sequence in logprobs_list:
        for token in sequence:
            for token_id in token:
                token[token_id]['logprob'] = str(token[token_id]['logprob'])
    return logprobs_list

def convert_to_jsonl(data_path, out_path):
    with open(data_path, "rb") as infile, open(out_path, "wb") as outfile:
        for item in ijson.items(infile, "item"):  # iterate over each object in array
            item['pass@1'] =str(item['pass@1'])
            item['logprobs_list'] = clean_logprobs(item['logprobs_list'])
            line = orjson.dumps(item) + b"\n"
            outfile.write(line)
            
# convert_to_jsonl(data_path, out_path)

    


In [ ]:
from numpy import mean


def top20_logprob_sum_f(sample: dict):
    top20 = []
    for sequence in sample["logprobs_list"]:
        top20seq = []
        count = 0                               #count = Token-Nr. (beginnend mit 0)
        for token in sequence:
            top20seq.append(0)
            for k in token.values():
                if (k["rank"]>= 1) and (k["rank"]<= 20):
                    top20seq[count]+= float (k["logprob"])
            count += 1
        top20.append(top20seq)
    return top20


def search(sample:dict):
    coding_tok_list = []
    for sequence in sample["logprobs_list"]:
        token_list = []

        index = 0
        for token in sequence:
            token_list.append(0)
            for id, k in token.items():
                if k["rank"]==1:
                    token_list[index]= id
            index += 1

        position = []
        for i in range(0,len(token_list)-2):
            if token_list[i]=='73594' and token_list[i+1]=='12669':
                if token_list[i+2]=='198':
                    position.append(i+3)
                else:
                    position.append(i+2)

        if len(position)>1:
            pos = position[-1]
            position = []
            position.append(pos)

        if len(position)==1:
            for j in range(position[0],len(token_list)-1):
                if token_list[j]=='73594':
                    position.append(j-1)
                elif token_list[j]=='13874' and token_list[j+1]=='19324':
                    position.append(j-1)
                    
        
        if len(position)>2:
            position = [position[0]]

        coding_tok_list.append(position)

    return coding_tok_list

def coding_logprob_f(position_list, logprob_list):
    coding_logprobs = {}
    first_token = []
    first_20_token = []
    last_token = []
    last_20_token= []

    if len(position_list)==len(logprob_list):
        for seq in range(0,len(logprob_list)):
            seq_logprobs = logprob_list[seq]
            seq_positions = position_list[seq]

            if len(seq_positions)>=1 and len(seq_positions)<3:
                first_token.append(seq_logprobs[(seq_positions[0])])

                if (seq_positions[0]+20)<=(len(seq_logprobs)-1):
                    first_20_token.append(float (mean(seq_logprobs[(seq_positions[0]):(seq_positions[0]+20)])))
                else:
                    first_20_token.append([])
                
                if len(seq_positions)==2:
                    last_token.append(seq_logprobs[(seq_positions[1])])
                    last_20_token.append(float (mean(seq_logprobs[(seq_positions[1]-19):(seq_positions[1]+1)])))
                else:
                    last_20_token.append([])
                    last_token.append([])


            else:
                first_token.append([])
                first_20_token.append([])
                last_20_token.append([])
                last_token.append([])

    coding_logprobs = {
        "first_token": first_token,
        "first_20_token": first_20_token,
        "last_token": last_token,
        "last_20_token": last_20_token
    }

    
    return coding_logprobs


def test(sample):
    hit = []
    for sequence in sample["logprobs_list"]:
        hit_seq = []
        index = 0                               #count = Token-Nr. (beginnend mit 0)
        for token in sequence:
            for id, k in token.items():
                if k["rank"]==1 and (k["decoded_token"].find("``")!= -1):
                    hit_seq.append([id,index])
                    
            index += 1
        hit.append(hit_seq)
    print(hit)


        

def prepare_sample(sample: dict):
    logprobs = [
                [
                    k["logprob"] for d in sequence for k in filter(lambda x: x["rank"] == 1, d.values())
                ] for sequence in sample["logprobs_list"]
            ]
    
    logprob_sum = top20_logprob_sum_f(sample)
    coding_tok_pos = search(sample)
    coding_log_probs = coding_logprob_f(coding_tok_pos,logprob_sum)

    test(sample)

    return {
        "id": sample["question_id"],
        "name": sample["question_title"],
        "prompt": sample["question_content"],
        "program": sample["code_list"],
        "language": 'python',
        "output_size": [len(output) for output in sample["output_list"]],
        "token_count": [len(logprobs) for logprobs in sample["logprobs_list"]],
        "is_correct": sample["graded_list"],
        "token_logprobs": logprobs,
        'cumulative_logprob': [sum([float(x) for x in l]) for l in logprobs],
        "top_logprobs_first_token": [sequence[0] for sequence in logprob_sum],
        "top_logprobs_first_20_tokens": [(float (mean(sequence[0:20]))) for sequence in logprob_sum],
        "top_logprobs_last_token": [sequence[-1] for sequence in logprob_sum],
        "top_logprobs_last_20_tokens": [(float (mean(sequence[(len(sequence)-20):(len(sequence))]))) for sequence in logprob_sum],
        "top_logprobs_first_coding_token":coding_log_probs["first_token"],
        "top_logprobs_first_20_coding_tokens":coding_log_probs["first_20_token"],
        "top_logprobs_last_coding_tokens": coding_log_probs["last_token"],
        "top_logprobs_last_20_coding_tokens":coding_log_probs["last_20_token"],
        "difficulty": sample["difficulty"],
    }

In [4]:
i=0
results = []
with open(jsonlines, "rb") as f:   
    for line in f:
        if i>=20:
            break
        obj = orjson.loads(line)
        sample = prepare_sample(obj)
        results.append(sample)
        print(sample)
        i+=1

{'id': '1873_A', 'name': 'A. Short Sort', 'prompt': 'There are three cards with letters $\\texttt{a}$, $\\texttt{b}$, $\\texttt{c}$ placed in a row in some order. You can do the following operation at most once: \n\n \n-  Pick two cards, and swap them.  Is it possible that the row becomes $\\texttt{abc}$ after the operation? Output "YES" if it is possible, and "NO" otherwise.\n\nInput\n\nThe first line contains a single integer $t$ ($1 \\leq t \\leq 6$)\xa0— the number of test cases.\n\nThe only line of each test case contains a single string consisting of each of the three characters $\\texttt{a}$, $\\texttt{b}$, and $\\texttt{c}$ exactly once, representing the cards.\n\nOutput\n\nFor each test case, output "YES" if you can make the row $\\texttt{abc}$ with at most one operation, or "NO" otherwise.\n\nYou can output the answer in any case (for example, the strings "yEs", "yes", "Yes" and "YES" will be recognized as a positive answer).Sample Input 1:\n6\n\nabc\n\nacb\n\nbac\n\nbca\n\nc

In [6]:
evaluation_data_path = "output/Qwen3-Coder-30B-A3B/preprocessed/codegeneration_10_0.2.jsonl"

# with open(evaluation_data_path, "wb") as outfile:
#     for item in results:     
#         line = orjson.dumps(item) + b"\n"
#         outfile.write(line)

In [9]:
def preprocess_data(input_path, output_path, max_samples=None):
    i = 0
    with open(input_path, "rb") as infile, open(output_path, "wb") as outfile:
        for line in tqdm(infile):
            if max_samples and i>=max_samples:
                break
            obj = orjson.loads(line)
            sample = prepare_sample(obj)
            line = orjson.dumps(sample) + b"\n"
            outfile.write(line)
            i += 1

preprocess_data(jsonlines, evaluation_data_path)

1055it [04:04,  4.31it/s]


# Groups
- loc
- cyclomatic complexity
- len output
- len code
- difficulty
- len prompt
- language

(identifier count, etc)

# Metrics
- mean logprob
@ Katharina:
- sum top-20 logprobs (last n tokens, last token, last code token, first token)
    - 1) last 20 tokens (Konfigurierbar für n)
    - 2) last token
    - 3) first 20 tokens
    - 4) last 20 code tokens
    - 5) last code token
    - 6) first code token